In [1]:
import itertools
import json
import nilearn
import os
import nilearn
import nibabel as nib
import numpy as np
import pandas as pd
import seaborn as sns
import sklearn

from pathlib import Path
from os import listdir as ls
from os.path import basename as bname
from os.path import dirname as dname
from os.path import expanduser as xpu
from os.path import join as pjoin
from pandas import DataFrame as df
from tqdm import tqdm
from typing import Sequence, Union
from collections.abc import Iterable

from nilearn import masking
from nilearn.connectome import ConnectivityMeasure
from nilearn.image import concat_imgs, iter_img, mean_img
from nilearn.input_data import NiftiMasker, NiftiMapsMasker, NiftiLabelsMasker

from nilearn import plotting
import nilearn.decoding
from nilearn.input_data import NiftiMasker
from nilearn.plotting import plot_stat_map, plot_anat, plot_img, plot_epi
from nilearn.glm.first_level import FirstLevelModel, make_first_level_design_matrix  

import cimaqprep
import loadutils as lu
import sniffbytes as snif
import scanzip as szip

from sklearn.feature_selection import f_classif
from sklearn.model_selection import KFold

/home/fnadeau/myenv/lib/python3.7/site-packages/nilearn/datasets/__init__.py:89: FutureWarning: Fetchers from the nilearn.datasets module will be updated in version 0.9 to return python strings instead of bytes and Pandas dataframes instead of Numpy arrays.
  "Numpy arrays.", FutureWarning)


In [2]:
cimaq_files_dir = xpu('~/../../data/simexp/DATA/cimaq_decoding_files')
paths_of_interest = {'cimaq_nov_dir':xpu('~/../../data/simexp/DATA/cimaq_20190901'),
                     'cimaq_mar_dir':xpu('~/../../data/simexp/DATA/cimaq_03-19'),
                     'events_dir':pjoin(cimaq_files_dir, 'events'),
                     'behav_dir':pjoin(cimaq_files_dir, 'behavioural'),
                     'masker_params_dir':pjoin(cimaq_files_dir, 'cimaq_common_masker_params.json')}
#                      'atlas_dir':xpu('~/../../data/neuromod/DATA/DiFuMo/')}
import warnings
warnings.filterwarnings('ignore')
from os.path import expanduser as xpu
from cimaqprep.participant_data import participant_data
subject00, subject01 = participant_data(**paths_of_interest), participant_data(**paths_of_interest)

fetching in-scan events: 100%|███████████████| 95/95 [00:00<00:00, 7548.00it/s]
computing trial durations: 120it [00:00, 7072.83it/s]
fetching out-scan behavioural data: 100%|███| 95/95 [00:00<00:00, 12747.42it/s]
finding correct spatial answers: 117it [00:00, 425.38it/s]
computing spatial accuracy: 117it [00:00, 7254.22it/s]
fetching in-scan events: 100%|██████████████| 95/95 [00:00<00:00, 18958.88it/s]
computing trial durations: 120it [00:00, 6355.57it/s]
fetching out-scan behavioural data: 100%|███| 95/95 [00:00<00:00, 18319.95it/s]
finding correct spatial answers: 117it [00:00, 395.49it/s]
computing spatial accuracy: 117it [00:00, 7535.72it/s]
fetching confounds: 100%|██████████████████| 101/101 [00:00<00:00, 1778.37it/s]


In [3]:
# subject00.nifti_masker = subject00.nifti_masker.fit(imgs=subject00.mar_scans.func[1][0])

In [4]:
difumo64 = \
    nilearn.datasets.fetch_atlas_difumo(dimension=64,
                                        resolution_mm=3,
                                        data_dir=xpu('~/../../data/neuromod/DATA/DiFuMo/'),
                                        resume=True,
                                        verbose=1)
difumo128 = \
    nilearn.datasets.fetch_atlas_difumo(dimension=128,
                                        resolution_mm=3,
                                        data_dir=xpu('~/../../data/neuromod/DATA/DiFuMo/'),
                                        resume=True,
                                        verbose=1)
difumo1024 = \
    nilearn.datasets.fetch_atlas_difumo(dimension=1024,
                                        resolution_mm=3,
                                        data_dir=xpu('~/../../data/neuromod/DATA/DiFuMo/'),
                                        resume=True,
                                        verbose=1)

In [5]:
subject00.maps_masker_params = dict(mask_img=subject00.mar_epi_mask,
                                    maps_img=difumo128.maps,
                                    allow_overlap=True,
                                    resampling_target='mask',
                                    **subject00.common_masker_params)
subject00.maps_masker = \
    nilearn.input_data.NiftiMapsMasker(**subject00.maps_masker_params).fit()

In [6]:
subject00.maps_maps_region_signals = \
    subject00.maps_masker.transform_single_imgs(imgs=subject00.mar_scans.func[1][0],
                                                confounds=subject00.confounds)

In [7]:
subject00.maps_maps_inverse_func = \
    subject00.maps_masker.inverse_transform(region_signals=subject00.maps_maps_region_signals)

In [8]:
# subject00.nifti_masker.fit(imgs=subject00.mar_scans.func[1][0])
# subject00.nifti_masker.generate_report()
# help(cimaqprep.resample_fmri_to_events)
subject00.new_func = subject00.resample_fmri_to_events(func_img=subject00.maps_maps_inverse_func,
#                                                        mask_img=subject00.mar_epi_mask,
                                                       n_events=subject00.events.shape[0]-4,
                                                       frame_times=list(subject00.frame_times)[3:-1])
#                                                        clean_resampled_imgs=False)

resampling fMRI image to events lenght: 100%|█| 116/116 [00:17<00:00,  6.57it/s


In [60]:
subject00.resampled_func = subject00.resample_fmri_to_events(func_img=subject00.mar_scans.func[1][0],
#                                                        mask_img=subject00.mar_epi_mask,
                                                       n_events=subject00.events.shape[0]-4,
                                                       frame_times=list(subject00.frame_times)[3:-1])
#                                                        clean_resampled_imgs=False)

resampling fMRI image to events lenght: 100%|█| 116/116 [00:13<00:00,  8.75it/s


In [80]:
help(FirstLevelModel)
# help(make_first_level_design_matrix)

Help on class FirstLevelModel in module nilearn.glm.first_level.first_level:

class FirstLevelModel(nilearn.glm._base.BaseGLM)
 |  FirstLevelModel(t_r=None, slice_time_ref=0.0, hrf_model='glover', drift_model='cosine', high_pass=0.01, drift_order=1, fir_delays=[0], min_onset=-24, mask_img=None, target_affine=None, target_shape=None, smoothing_fwhm=None, memory=Memory(location=None), memory_level=1, standardize=False, signal_scaling=0, noise_model='ar1', verbose=0, n_jobs=1, minimize_memory=True, subject_label=None)
 |  
 |  Implementation of the General Linear Model
 |  for single session fMRI data.
 |  
 |  Parameters
 |  ----------
 |  t_r : float
 |      This parameter indicates repetition times of the experimental runs.
 |      In seconds. It is necessary to correctly consider times in the design
 |      matrix. This parameter is also passed to nilearn.signal.clean.
 |      Please see the related documentation for details.
 |  
 |  slice_time_ref : float, optional
 |      This para

/home/fnadeau/myenv/lib/python3.7/site-packages/nilearn/glm/__init__.py:56: FutureWarning: The nilearn.glm module is experimental. It may change in any future release of Nilearn.
  'It may change in any future release of Nilearn.', FutureWarning)
/home/fnadeau/myenv/lib/python3.7/site-packages/nilearn/glm/__init__.py:56: FutureWarning: The nilearn.glm module is experimental. It may change in any future release of Nilearn.
  'It may change in any future release of Nilearn.', FutureWarning)
/home/fnadeau/myenv/lib/python3.7/site-packages/nilearn/glm/__init__.py:56: FutureWarning: The nilearn.glm module is experimental. It may change in any future release of Nilearn.
  'It may change in any future release of Nilearn.', FutureWarning)
/home/fnadeau/myenv/lib/python3.7/site-packages/nilearn/glm/__init__.py:56: FutureWarning: The nilearn.glm module is experimental. It may change in any future release of Nilearn.
  'It may change in any future release of Nilearn.', FutureWarning)
/home/fnadea

In [81]:
common_glm_matrix_params = \
    {'hrf_model':'spm + derivative',
     'drift_model':'cosine',
     'high_pass':0.09,
     'drift_order':1,
     'fir_delays':[0],
     'min_onset':0}
def make_glm_and_matrix(subject:object, **kwargs):
    # smoothing fwhm value criterion
    '''
    Source: http://jpeelle.net/mri/image_processing/smoothing.html
    One common rule of thumb is that, to render your data approximately normal,
    you should smooth with a Gaussian filter approximately three times the size of your voxel.
    If your voxel size is 3 x 3 x 3 mm, you would smooth with a 9 mm FWHM Gaussian filter.
    
    hrf_models available: # ['glover', 'spm', 'spm + derivative', 'spm + derivative + dispersion',
                             'glover + derivative', 'glover + derivative + dispersion', 'fir', None]
    '''

    from nilearn.glm.first_level import FirstLevelModel
    from nilearn.glm.first_level import make_first_level_design_matrix
    first_level_model = FirstLevelModel(t_r=subject.t_r,
                                        slice_time_ref=0.0,
                                        hrf_model='spm',
                                        drift_model=None,
#                                         hrf_model='glover', 
#                                         drift_model='cosine', # Can be 'polynomial', 'cosine' or None. Default='cosine'.
#                                         high_pass=0.09,
#                                         low_pass=0.21,
#                                         drift_order=1, # Default
#                                         fir_delays=[0], # Default
                                        min_onset=subject.events.onset[3],
#                                         mask_img=subject.maps_masker.mask_img,
                                        mask_img=False,
                                        smoothing_fwhm=0,
#                                         target_affine=subject.mar_epi_mask.affine,
#                                         target_shape=subject.mar_epi_mask.shape,
#                                         smoothing_fwhm=dict(nib.load(subject.mar_scans.func[1][0]).header)['pixdim'][1]*3,
    #                                     memory=Memory(location=None),
                                        memory_level=1,
                                        standardize=False,
                                        signal_scaling=0,
                                        noise_model='ar1',
                                        verbose=0,
                                        n_jobs=8,
                                        minimize_memory=False,
                                        subject_label=subject.sub_id[0])
#                                           **kwargs)
    # Create First Level Design Matrix
    fmri_design_matrix = \
        make_first_level_design_matrix(
    #         frame_times=train.dropna()[0],
            frame_times=subject.resampled_frame_times[3:-1],
    #         frame_times=np.arange(0, subject.frame_times.max(),
    #                                           subject.frame_times.max()/subject.events.shape[0]),
    #         events=subject.events[['onset','duration','trial_type']],
            events=subject.events.iloc[3:-1,:][['onset','duration','outcomes']].rename(
                columns=({'outcomes':'trial_type'})),
            hrf_model='spm',
            drift_model=None)
#             hrf_model='glover',
#             drift_model='cosine',
#             high_pass=0.09,
#             low_pass=0.21,
#             drift_order=1,
#             fir_delays=[0],
    #         add_regs=subject.resampled_confounds.fillna(0).values,
    #         add_reg_names=list(col.replace('.','_') for col in subject.resampled_confounds.columns),
#             oversampling=50)
#             **kwargs)
    return first_level_model, fmri_design_matrix
first_level_model00, fmri_design_matrix00 = \
     make_glm_and_matrix(subject=subject00)
#                          **common_glm_matrix_params)

In [82]:
first_level_model00.fit(run_imgs=subject00.new_func,
#                       events=subject00.events[['onset','duration','outcomes']].rename(columns={'outcomes':'trial_type'}),
#                       confounds=subject_data.confounds,
                      design_matrices=fmri_design_matrix00,
                      bins=fmri_design_matrix00.shape[0])

FirstLevelModel(drift_model=None, hrf_model='spm',
                mask_img=<nibabel.nifti1.Nifti1Image object at 0x7fe83e70b110>,
                min_onset=24.066, minimize_memory=False, n_jobs=8,
                signal_scaling=True, smoothing_fwhm=0,
                subject_label='sub-370092', t_r=2.5000002)

In [83]:
# Define desired contrasts names
new_contrast_names = list(str((itm[0],'- '+itm[1]))[1:-1].replace(
    "'",'').replace(',','') for itm in
     itertools.combinations([col for col in
                             list(fmri_design_matrix00.columns)
                             if 'drift' not in col],2))
new_contrast_names = [name.replace('.','_') for name in new_contrast_names]
contrast_params =\
{       'contrasts':list(fmri_design_matrix00.columns)[:4]+new_contrast_names,
#              +new_contrast_names,
        'title':str(subject00.sub_id)+' report',
#         'bg_img':subject00.mar_epi_mask,
#         'bg_img':mean_img(difumo64.maps)
        'bg_img':subject00.mar_scans.anat[1][2],
#         'threshold':3.09,
        'alpha':0.001,
        'cluster_threshold':3,
        'height_control':'fpr',
        'min_distance':3.0,
        'plot_type':'slice',
#         'display_mode':None,
#         'report_dims':(1600, 800)
}
# Model Fitting


# report00 = first_level_model00.generate_report(**contrast_params)


In [84]:
report00 = first_level_model00.generate_report(**contrast_params)

In [85]:
report00

/home/fnadeau/myenv/lib/python3.7/site-packages/nilearn/glm/__init__.py:56: FutureWarning: The nilearn.glm module is experimental. It may change in any future release of Nilearn.
  'It may change in any future release of Nilearn.', FutureWarning)
/home/fnadeau/myenv/lib/python3.7/site-packages/nilearn/glm/__init__.py:56: FutureWarning: The nilearn.glm module is experimental. It may change in any future release of Nilearn.
  'It may change in any future release of Nilearn.', FutureWarning)
/home/fnadeau/myenv/lib/python3.7/site-packages/nilearn/glm/__init__.py:56: FutureWarning: The nilearn.glm module is experimental. It may change in any future release of Nilearn.
  'It may change in any future release of Nilearn.', FutureWarning)
/home/fnadeau/myenv/lib/python3.7/site-packages/nilearn/glm/__init__.py:56: FutureWarning: The nilearn.glm module is experimental. It may change in any future release of Nilearn.
  'It may change in any future release of Nilearn.', FutureWarning)
/home/fnadea

In [ ]:
nilearn.plotting.plot_prob_atlas(maps_img=subject00.maps_maps_inverse_func,
                                 view_type='auto',
                                 colorbar=True)


In [ ]:
from nilearn.decomposition import DictLearning
dictlearning_params = dict(n_components=20,
                           n_epochs=1,
                           alpha=10,
                           reduction_ratio='auto',
                           dict_init=subject00.maps_maps_inverse_func,
                           random_state=None,
                           batch_size=20,
                           method='cd',
                           mask=subject00.labels_masker,
                           target_affine=subject00.maps_masker.mask_img_.affine,
                           target_shape=subject00.maps_masker.mask_img_.shape,
                           mask_strategy='epi',
                           mask_args=None,
                           smoothing_fwhm=9,
                           standardize=True,
                           detrend=True,
                           high_pass=0.09,
                           low_pass=0.21,
                           t_r=2.5,
                           memory_level=1,
                           n_jobs=-1)
subject00.dictlearning = DictLearning(**dictlearning_params).fit(imgs=subject00.mar_scans.func[1][0],
                                                               confounds=subject00.confounds)

In [ ]:
subject00.loading = subject00.dictlearning.transform(imgs=[subject00.mar_scans.func[1][0]],
                                                     confounds=[subject00.confounds])

In [ ]:
subject00.dictlearning

In [ ]:
subject00.maps_maps_inverse_func.get_data() == \
    subject00.labels_labels_inverse_func.get_data()


# subject00.maps_elements_region_signals = \
#     subject00.maps_masker.transform(imgs=subject00.mar_scans.func[1][0],
#                                                 confounds=subject00.confounds)
# subject00.maps_elements_inverse_func = \
#     subject00.maps_masker.inverse_transform(subject00.maps_elements_region_signals)

In [ ]:
# Fit to data, then transform it
subject00.region_signals_X_new = \ 
    subject00.nifti_masker.fit_transform(X=subject00.mar_scans.func[1][0],
                                         y=None,
                                         confounds=subject00.confounds,
                                         sample_mask=None)
# Fit to data, then transform it
subject00.region_signals_voxels_X_new = \
    subject00.nifti_masker.fit_transform(X=subject00.mar_scans.func[1][0],
                                         y=subject00.region_signals_voxels,
                                         confounds=subject00.confounds,
                                         sample_mask=None)
# Fit to data, then transform it
subject00.region_signals_elements_X_new = \
    subject00.nifti_masker.fit_transform(X=subject00.mar_scans.func[1][0],
                                         y=subject00.region_signals_elements,
                                         confounds=subject00.confounds,
                                         sample_mask=None)

# subject00.region_signals_elements = \ # Applies mask
#     subject00.nifti_masker.transform(imgs=subject00.mar_scans.func[1][0],
#                                      confounds=subject00.confounds,
#                                      sample_mask=None)

In [ ]:
# Inverse transform of prevously extracted signals
# subject00.inv_transform_voxels = \
#     subject00.nifti_masker.inverse_transform(X=subject00.region_signals_voxels)
# subject00.inv_transform_elements = \
#     subject00.nifti_masker.inverse_transform(X=subject00.region_signals_elements)
# subject00.inv_transform_X_new = \
#     subject00.nifti_masker.inverse_transform(X=subject00.region_signals_X_new)

In [ ]:
# thresholding_strategy : str {'ratio_n_voxels', 'img_value', 'percentile'}
region_extractor_params = dict(maps_img=subject00.maps_maps_inverse_func,
                               mask_img=subject00.mar_epi_mask,
                               min_region_size=1350,
                               threshold=1.0,
                               thresholding_strategy='ratio_n_voxels',
                               extractor='local_regions',
                               min_region_size=1350
                               **subject00.common_masker_params)
#                                smoothing_fwhm=6,
#                                standardize=False,
#                                detrend=False,
#                                low_pass=None,
#                                high_pass=None,
#                                t_r=None,
#                                memory=Memory(location=None),
#                                memory_level=0,
#                                verbose=0)

In [ ]:
from nilearn.regions import RegionExtractor
help(RegionExtractor)

In [ ]:
# Import Region Extractor algorithm from regions module
# threshold=0.5 indicates that we keep nominal of amount nonzero voxels across all
# maps, less the threshold means that more intense non-voxels will be survived.
from nilearn.regions import RegionExtractor
extractor = RegionExtractor(**region_extractor_params)

# Just call fit() to process for regions extraction
extractor.fit()
# Extracted regions are stored in regions_img_
regions_extracted_img = extractor.regions_img_
# Each region index is stored in index_
regions_index = extractor.index_
# Total number of regions extracted
n_regions_extracted = regions_extracted_img.shape[-1]

# Visualization of region extraction results
title = ('%d regions are extracted from %d components.'
         '\nEach separate color of region indicates extracted region'
         % (n_regions_extracted, 8))
plotting.plot_prob_atlas(regions_extracted_img, view_type='filled_contours',
                         title=title)

In [ ]:
subject00.intersect_masker = nilearn.masking.intersect_masks(
                                mask_imgs=[
                                    subject00.labels_masker.mask_img,
                                    subject00.maps_masker.mask_img,
                                    subject00.nifti_masker.mask_img],
                                                             threshold=0.5,
                                                             connected=True)

In [ ]:
subject00.labels_masker = subject00.labels_masker.fit()
subject00.maps_masker = subject00.maps_masker.fit()
# subject00.nifti_masker.fit()

In [ ]:
def get_dictlearn_params(subject:object, **kwargs)->dict:
    mask_args00 = \
    {'allow_overlap': True,
     'resampling_target': 'mask',
     **subject00.common_masker_params}
#      'bg_img':mean_img(anat00)}
    dictlearn_params = \
        {'mask':subject00.maps_masker.masj_img,
         'n_components': 10,
         'n_epochs': subject00.events.iloc[3:-1,:].shape[0],
         'alpha': 10,
         'reduction_ratio': 'auto',
#          'dict_init': None,
         'dict_init': difumo64.maps,
         'random_state': None,
         'batch_size': 2,
         'method': 'cd',
         'mask': subject00.nifti_masker.mask_img,
         'smoothing_fwhm':9,
#          'smoothing_fwhm': dict(nib.load(subject.mar_scans.anat[1][0]).header)['pixdim'][1]*3,
         'standardize': True,
         'detrend': False,
#          'low_pass': 0.21,
#          'low_pass':1.0,
#          'high_pass': 0.09,
         't_r': subject.t_r,
#          'target_affine': subject00.masker.target_affine,
#          'target_shape': subject00.masker.target_shape,
         'mask_strategy': 'epi'}
#          'mask_args':mask_args00}
    return dictlearn_params
dictlearn_params00=get_dictlearn_params(subject00)

In [ ]:
dictlearn00 = \
    nilearn.decomposition.DictLearning(**dictlearn_params00)

In [ ]:
dictlearn00 = dictlearn00.fit()
#     y=difumo64.labels,
#     confounds=subject00.confounds)

In [ ]:
subject00.loadings = dictlearn00.transform(imgs=subject00.masked_func)


In [ ]:
nilearn.plotting.plot_prob_atlas(dictlearn00.components_img_,
                                 view_type='filled_contours')

In [ ]:
anat_bg_mask = \
    nilearn.masking.compute_background_mask(data_imgs=concat_imgs(subject00.mar_scans.anat[1],
                                                                  auto_resample=True),
                                            border_size=2,
                                            connected=False,
                                            opening=True,
                                            target_affine=subject00.mar_epi_mask.affine,
                                            target_shape=subject00.mar_epi_mask.shape,
                                            memory=None,
                                            verbose=0)

In [ ]:
anat00 = cimaqprep.resample_fmri_to_mask(concat_imgs(subject00.mar_scans.anat[1],
                                                     auto_resample=True),
                                         subject00.masker.mask_img)
# subject00.masker.mask_img == subject00.masker.mask_img_

In [ ]:
contrasts00 = \
    [first_level_model00.compute_contrast(contrast_def=key,
                                     output_type='all')
     for key in tqdm(list(basic_contrasts00.keys()),
                     desc='computing contrasts')]

In [ ]:
import nilearn.decoding
from sklearn.model_selection import KFold
cv = KFold(n_splits=4)
searchlight = nilearn.decoding.SearchLight(mask_img=subject00.mar_epi_mask,
                                           process_mask_img=process_mask_img,
                                           radius=4.5,
                                           estimator='svc',
                                           n_jobs=1,
                                           scoring=None,
                                           cv=cv,
                                           verbose=1)

In [ ]:
searchlight.fit(imgs=concat_imgs(list(iter_img(subject00.cleaned_func))[3:-1]),
                y=subject00.events.iloc[3:-1,:]['outcomes'].values.tolist())
# help(nilearn.decoding.SearchLight)

In [ ]:
# F-score computation
from nilearn.input_data import NiftiMasker

# For decoding, standardizing is often very important
nifti_masker = NiftiMasker(mask_img=mask_img, sessions=None,
                           standardize=True)
#                            memory='nilearn_cache',
#                            memory_level=1)
fmri_masked = nifti_masker.fit_transform(concat_imgs(list(iter_img(subject00.cleaned_func))[3:-1]))

In [ ]:


from sklearn.feature_selection import f_classif
f_values, p_values = f_classif(fmri_masked, y=subject00.events.iloc[3:-1,:]['outcomes'].values.tolist())
p_values = -np.log10(p_values)
p_values[p_values > 10] = 10
p_unmasked = nilearn.image.get_data(nifti_masker.inverse_transform(p_values))



In [ ]:
subject00_resampled_anat = [(bname(anat_img), nilearn.image.resample_img(img=anat_img,
                                                       target_affine=subject00.mar_epi_mask.affine,
                                                       target_shape=subject00.mar_epi_mask.shape,
                                                       interpolation='continuous',
                                                       copy=True, order='F', clip=True,
                                                       fill_value=0,
                                                       force_resample=True))
  for anat_img in subject00.mar_scans.anat[1].tolist()]

In [ ]:
from nilearn import image
from nilearn.image import new_img_like
mean_fmri = image.mean_img(concat_imgs(list(iter_img(subject00.cleaned_func))[3:-1]))

from nilearn.plotting import plot_stat_map, plot_img, show
searchlight_img = new_img_like(mean_fmri, searchlight.scores_)

# Because scores are not a zero-center test statistics, we cannot use
# plot_stat_map
[plot_img(img=searchlight_img,
          bg_img=anat_img[1],
          title="Searchlight {anat_img}".format(anat_img=anat_img[0]),
          display_mode="ortho",
#          cut_coords=[-9],
          vmin=.42,
          cmap='hot',
          threshold=.2,
          black_bg=True)
 for anat_img in subject00_resampled_anat]

# F_score results
# p_ma = np.ma.array(p_unmasked, mask=np.logical_not(process_mask))
# f_score_img = new_img_like(mean_fmri, p_ma)
# plot_stat_map(stat_map_img=f_score_img,
#               bg_img=subject00.mar_scans.anat[1][2],
#               title="F-scores", display_mode="ortho",
# #               cut_coords=[-9],
#               colorbar=True)

show()

In [ ]:
# Make processing parallel
# /!\ As each thread will print its progress, n_jobs > 1 could mess up the
#     information output.

# Define the cross-validation scheme used for validation.
# Here we use a KFold cross-validation on the session, which corresponds to
# splitting the samples in 4 folds and make 4 runs using each fold as a test
# set once and the others as learning sets

# The radius is the one of the Searchlight sphere that will scan the volume

cv = KFold(n_splits=4)


searchlight = nilearn.decoding.SearchLight(
    mask_img,
    process_mask_img=None,
    radius=5.6, n_jobs=1,
    verbose=1, cv=cv)


In [ ]:
rez=first_level_model00.__dict__['results_'][0][0.0]
dict(tuple((key, rez.__dict__[key]) for key in list(rez.__dict__.keys())))

In [ ]:
from nilearn.input_data import NiftiMasker, NiftiLabelsMasker
labelsmasker00=NiftiLabelsMasker(labels_img=list(iter_img(difumo.maps))[0],
                                 labels=difumo.labels,
                                 background_label=0,
                                 mask_img=subject00.mar_epi_mask,
                                 smoothing_fwhm=9.0,
                                 standardize=True,
                                 standardize_confounds=True,
                                 high_variance_confounds=True,
                                 detrend=False,
                                 low_pass=0.21,
                                 high_pass=0.09,
                                 t_r=subject00.t_r,
                                 dtype=float,
                                 resampling_target='labels',
                                 memory_level=1,
                                 verbose=0,
                                 strategy='mean',
                                 reports=True)

In [ ]:
labelsmasker00.fit_transform(imgs=subject00.cleaned_func,
                                                         confounds=None,
                                                         sample_mask=None)

In [ ]:


# create masker to extract functional data within atlas parcels
masker = NiftiMapsMasker(maps_img=difumo.maps,
                         mask_img=subject00.mar_epi_mask,
                         standardize=True,
                         allow_overlap=True,
                         smoothing_fwhm=9.0,
                         standardize_confounds=True,
                         high_variance_confounds=True,
                         detrend=False,
                         low_pass=0.21,
                         high_pass=0.09,
                         t_r=subject00.t_r,
                         dtype=float,
                         resampling_target='maps',
                         memory_level=1,
                         verbose=0)
#                          memory='nilearn_cache')
connectome_measure = ConnectivityMeasure(kind='correlation')
masker.fit()
# extract time series from all subjects and concatenate them
time_series = masker.transform_single_imgs(imgs=subject00.cleaned_func)
#                                            sample_mask=subject00.masker)

In [ ]:
# Has to be written between brackets to avoid dimensionality-related error
correlation_matrices = connectome_measure.fit([time_series])

In [ ]:

# time_series = []
# for func, confounds in zip(subject00.cleaned_func, subject00.confounds):
#     time_series.append(masker.fit_transform(func, confounds=confounds))

# calculate correlation matrices across subjects and display
correlation_matrices = connectome_measure.fit_transform([time_series])

# Mean correlation matrix across 10 subjects can be grabbed like this,
# using connectome measure object
mean_correlation_matrix = connectome_measure.mean_

# grab center coordinates for probabilistic atlas
coordinates = nilearn.plotting.find_probabilistic_atlas_cut_coords(maps_img=difumo.maps)

In [ ]:
# plot connectome with 85% edge strength in the connectivity
nilearn.plotting.plot_connectome(mean_correlation_matrix, coordinates,
                                 edge_threshold="85%",
                                 title='DiFuMo with {0} dimensions (probabilistic)'.format(64))
nilearn.plotting.show()

In [ ]:
NiftiMapsMasker(maps_img, mask_img=None, allow_overlap=True,
                smoothing_fwhm=None, standardize=False, standardize_confounds=True,
                high_variance_confounds=False, detrend=False, low_pass=None, high_pass=None,
                t_r=None, dtype=None,
                resampling_target='data', memory=Memory(location=None), memory_level=0, verbose=0)

In [ ]:
from nilearn.input_data import NiftiLabelsMasker
from nilearn.connectome import ConnectivityMeasure

# ConenctivityMeasure from Nilearn uses simple 'correlation' to compute
# connectivity matrices for all subjects in a list
connectome_measure = ConnectivityMeasure(kind='correlation')

# useful for plotting connectivity interactions on glass brain


# create masker to extract functional data within atlas parcels
masker = NiftiLabelsMasker(labels_img=yeo['thick_17'], standardize=True,
                           memory='nilearn_cache')

# extract time series from all subjects and concatenate them
time_series = []
for func, confounds in zip(data.func, data.confounds):
    time_series.append(masker.fit_transform(func, confounds=confounds))

# calculate correlation matrices across subjects and display
correlation_matrices = connectome_measure.fit_transform(time_series)

# Mean correlation matrix across 10 subjects can be grabbed like this,
# using connectome measure object
mean_correlation_matrix = connectome_measure.mean_

# grab center coordinates for atlas labels
coordinates = plotting.find_parcellation_cut_coords(labels_img=yeo['thick_17'])

# plot connectome with 80% edge strength in the connectivity
plotting.plot_connectome(mean_correlation_matrix, coordinates,
                         edge_threshold="80%",
                         title='Yeo Atlas 17 thick (func)')

In [ ]:
# help(labelsmasker00.transform_single_imgs)
labelsmasker00.transform_single_imgs(difumo.maps)

In [ ]:
labelsmasker00_4d_transform = labelsmasker00.transform_single_imgs(imgs=subject00.cleaned_func)


In [ ]:
masked_imgs00 = subject00.masker.transform(imgs=subject00.cleaned_func)
masked_imgs01 = subject01.masker.transform(imgs=subject01.cleaned_func)
#                                confounds=subject00.confounds,
#                                sample_mask=nilearn.image.get_data(masker.mask_img_))

In [ ]:
import sklearn
import sklearn.svm
from sklearn.feature_selection import SelectKBest
# help(SelectKBest)
import scipy
from scipy.fftpack import fft
# help(fft)

In [ ]:
masked_func00 = nilearn.masking.apply_mask(imgs=subject00.cleaned_func,
                                         mask_img=subject00.masker.mask_img_,
                                         dtype='f',
                                         smoothing_fwhm=9.0,
                                         ensure_finite=True)

In [ ]:
from nilearn.input_data import NiftiLabelsMasker
from nilearn.connectome import ConnectivityMeasure

# ConenctivityMeasure from Nilearn uses simple 'correlation' to compute
# connectivity matrices for all subjects in a list
connectome_measure = ConnectivityMeasure(kind='correlation')

# useful for plotting connectivity interactions on glass brain
from nilearn import plotting

# create masker to extract functional data within atlas parcels
masker = NiftiLabelsMasker(labels_img=difumo.maps, standardize=True,
                           memory='nilearn_cache')

# extract time series from all subjects and concatenate them
time_series = []
for func, confounds in zip(data.func, data.confounds):
    time_series.append(masker.fit_transform(func, confounds=confounds))

# calculate correlation matrices across subjects and display
correlation_matrices = connectome_measure.fit_transform(time_series)

# Mean correlation matrix across 10 subjects can be grabbed like this,
# using connectome measure object
mean_correlation_matrix = connectome_measure.mean_

# grab center coordinates for atlas labels
coordinates = plotting.find_parcellation_cut_coords(labels_img=yeo['thick_17'])

# plot connectome with 80% edge strength in the connectivity
plotting.plot_connectome(mean_correlation_matrix, coordinates,
                         edge_threshold="80%",
                         title='Yeo Atlas 17 thick (func)')


In [ ]:
report00.save_as_html(pjoin(xpu('~/'),str(subject00.sub_id[0])+'_'+str(subject00.sub_id[1])))

In [ ]:
# Compute DiFuMo Atlas Masker
atlas_path=xpu('~/../../data/neuromod/DATA/DiFuMo/512/3mm/maps.nii.gz')
atlas_filename = nib.load(atlas_path)
labels = pd.read_csv(xpu('~/../../data/neuromod/DATA/DiFuMo/512/labels_512_dictionary.csv'))

# data,fmri_filenames=subject00, cleaned_fmri_imgs

from nilearn.input_data import NiftiLabelsMasker
masker00 = NiftiLabelsMasker(
#     labels_img=nilearn.image.mean_img(atlas_filename),
#                            labels_img=mean_img(concat_imgs(difumo['maps'])),
                           labels_img=mean_img(concat_imgs(difumo['maps'])),
                           labels=difumo['labels'],
                           background_label=0,
#                              mask_img=nilearn.image.mean_img(atlas_filename),
                           mask_img=subject00.mar_epi_mask,
                           smoothing_fwhm=9,
                           standardize=True,
                           standardize_confounds=True,
                           high_variance_confounds=True,
                           detrend=True,
                           low_pass=None, high_pass=None,
                           t_r=2.5, dtype=None,
                           resampling_target='data',
                           memory_level=1,
                           verbose=1, strategy='mean',
                             reports=True)


In [ ]:
test02=df(subject00.resampled_frame_times,columns=['onset'])
test02[['duration', 'trial_type']]=tuple(zip(test02.onset.diff().dropna().unique().tolist()*test02.shape[0],
                                             subject00.events.outcomes.fillna('ctl')))
# test02['trial_type']=subject00.events.outcomes.fillna('ctl').values.tolist()
events_=test02

In [ ]:
import numpy as np
import pandas as pd
from nilearn.glm.first_level import make_first_level_design_matrix

def make_design_matrices(fmri_img, events):
    design_matrices = []
    for idx, img in enumerate(fmri_img, start=1):
        # Build experimental paradigm
        n_scans = img.shape[-1]
#         events = pd.read_table(subject_data['events{}'.format(idx)])
        # Define the sampling times for the design matrix
        frame_times = np.arange(n_scans) * subject00.t_r
        # Build design matrix with the previously defined parameters
        design_matrix = make_first_level_design_matrix(
                frame_times,
                events,
                hrf_model='glover',
                drift_model='cosine',
    #             high_pass=high_pass,
                )
        # put the design matrices in a list
        design_matrices.append(design_matrix)
    return design_matrices
design_matrices = make_design_matrices(fmri_img=subject00.resampled_fmri_to_events.values,
                                       events=subject00.events[['onset','duration','outcomes']].rename(columns={'outcomes':'trial_type'}))

In [ ]:
from nilearn.input_data import NiftiLabelsMasker
from nilearn.connectome import ConnectivityMeasure

# ConenctivityMeasure from Nilearn uses simple 'correlation' to compute
# connectivity matrices for all subjects in a list
connectome_measure = ConnectivityMeasure(kind='correlation')

# useful for plotting connectivity interactions on glass brain
from nilearn import plotting

# create masker to extract functional data within atlas parcels
masker = NiftiLabelsMasker(labels_img=difumo['thick_17'], standardize=True,
                           memory='nilearn_cache')

# extract time series from all subjects and concatenate them
time_series = []
for func, confounds in zip(data.func, data.confounds):
    time_series.append(masker.fit_transform(func, confounds=confounds))

# calculate correlation matrices across subjects and display
correlation_matrices = connectome_measure.fit_transform(time_series)

# Mean correlation matrix across 10 subjects can be grabbed like this,
# using connectome measure object
mean_correlation_matrix = connectome_measure.mean_

# grab center coordinates for atlas labels
coordinates = plotting.find_parcellation_cut_coords(labels_img=difumo['thick_17'])

# plot connectome with 80% edge strength in the connectivity
plotting.plot_connectome(mean_correlation_matrix, coordinates,
                         edge_threshold="80%",
                         title='difumo Atlas 17 thick (func)')

We can specify basic contrasts (to get beta maps).
We start by specifying canonical contrast that isolate design matrix columns.
We actually want more interesting contrasts. The simplest contrast
just makes the difference between the two main conditions.  We
define the two opposite versions to run one-tailed t-tests.  We also
define the effects of interest contrast, a 2-dimensional contrasts
spanning the two conditions.

In [ ]:
computed_contrasts=[fmri_glm.compute_contrast(
                         contrast_val, output_type='z_score')
                    for contrast_id, contrast_val in contrasts.items()]

In [ ]:
import itertools
new_contrast_names = list(str((itm[0],'- '+itm[1]))[1:-1].replace(
    "'",'').replace(',','') for itm in
     itertools.combinations(names,2))
new_contrast_names
# basic_contrasts00[itm] = basic_contrasts00[itm.split(' - ')]
# [tuple(itm) for itm in new_contrast_names]


In [ ]:
# fit_model01=first_level_model00.fit(run_imgs=list(iter_img(concat_imgs(subject00.resampled_fmri_to_events.values))),
#                         design_matrices=design_matrices)

In [ ]:
# import nilearn.decoding

# # Define the cross-validation scheme used for validation.
# # Here we use a KFold cross-validation on the session, which corresponds to
# # splitting the samples in 4 folds and make 4 runs using each fold as a test
# # set once and the others as learning sets
# from sklearn.model_selection import KFold

# import nilearn.decoding
# # The radius is the one of the Searchlight sphere that will scan the volume
# searchlight = nilearn.decoding.SearchLight(
#     mask_img=subject_data.mar_epi_mask,
#     process_mask_img=nilearn.image.get_data(subject_data.mar_epi_mask).astype(np.int),
#     radius=5.6,
#     n_jobs=1,
#     verbose=1,
#     estimator=first_level_model00)

# Process Mask
mask_img = subject_data00.mar_epi_mask

# .astype() makes a copy.
process_mask00 = nilearn.image.get_data(mask_img).astype(np.int)
# picked_slice = 29
# process_mask[..., (picked_slice + 1):] = 0
# process_mask[..., :picked_slice] = 0
# process_mask[:, 30:] = 0
process_mask_img00 = nilearn.image.new_img_like(mask_img, process_mask00)

# Searchlight
from nilearn.decoding import SearchLight
searchlight=SearchLight(mask_img=subject_data00.mar_epi_mask
                                   , process_mask_img=process_mask_img00,
                                   radius=2.0, estimator=first_level_model00,
                                   n_jobs=1, scoring=None, cv=None, verbose=0)
# enc_ctl_report=fit_model00.generate_report(contrasts=list(fit_model00.design_matrices_[0].columns[:4])+['enc-ctl'],
#                                          bg_img=subject_data.mar_epi_mask)
# enc_ctl_report

In [ ]:
contrast_matrix = np.eye(fit_model.design_matrices_[0].shape[1])
basic_contrasts = dict([(column, contrast_matrix[i]) for i, column in
                        enumerate(fit_model.design_matrices_[0].columns[:5])])
# basic_contrasts['enc-hit']=basic_contrasts['enc']-basic_contrasts['hit']
# basic_contrasts['enc-miss']=basic_contrasts['enc']-basic_contrasts['miss']
basic_contrasts['ctl-hit']=basic_contrasts['ctl']-basic_contrasts['hit']
basic_contrasts['ctl-miss']=basic_contrasts['ctl']-basic_contrasts['miss']
basic_contrasts['ctl-false_alarm']=basic_contrasts['false_alarm']-basic_contrasts['ctl']
# basic_contrasts['enc-ctl']=basic_contrasts['enc']-basic_contrasts['ctl']
basic_contrasts['false_alarm-hit']=basic_contrasts['false_alarm']-basic_contrasts['hit']
# basic_contrasts['false_alarm-enc']=basic_contrasts['false_alarm']-basic_contrasts['enc']
basic_contrasts['false_alarm-miss']=basic_contrasts['false_alarm']-basic_contrasts['miss']
basic_contrasts['hit-miss']=basic_contrasts['hit']-basic_contrasts['miss']
# basic_contrasts['control']={basic_contrasts['ctl'],
#                             basic_contrasts['ctl-miss'],
#                             basic_contrasts['ctl-hit'],
#                             basic_contrasts['ctl-false_alarm']}
basic_contrasts

In [ ]:
def unzip_obj(src_path):
    with gzip.open(src_path, 'rb') as f_in:
        uzobj = f_in.read()
    f_in.close()
    return uzobj
def tmptargz(src_path):
    with tmpfile(prefix=os.getcwd()+"/",
                dir=os.path.splitext(topname)[0],
                suffix=None) as atar:
        BytesIO(unzip_obj(snif.get_bytes(pjoin(src_path, topname)))).write(atar)
        with tmpdir(prefix=os.getcwd()+"/",
                    dir=os.path.splitext(bname(atar.name))[0],
                    suffix="/") as adir:
            atar.write(adir.name)
    #             shutil.copytree(tardir, adir)
            print(ls(adir.name))
        adir.flush()
tmptargz(tardir)        